In [ ]:
%%capture

try:
    from tetraslab.dash import Dash
except ModuleNotFoundError:
    print("ModuleNotFoundError: No module named 'tetraslab', defaulting to regular Dash.")
    from dash import Dash
import importlib.util
import re
import amrlib
from amrlib.graph_processing.amr_plot import AMRPlot
import uuid
from IPython.display import SVG, display
import os
import shutil
import subprocess
from subprocess import Popen, PIPE, STDOUT
from glob import glob
import sys
import os
from IPython.display import HTML,IFrame
import ipywidgets
import dash_bootstrap_components as dbc
from dash import dcc, html, Input, Output
from dash.dependencies import Input, Output, State
import base64
import xml.etree.ElementTree as ET
import configparser

config = configparser.ConfigParser()
config.read('config.ini')
#config['LIB']['']

AMR_BATCH_PATH = config['LIB']['AMR_BATCH_PATH']
sys.path.insert(0, os.path.abspath(AMR_BATCH_PATH))
import amrbatch

TENET_PATH = config['LIB']['TENET_PATH']
sys.path.insert(0, os.path.abspath(TENET_PATH))
import tenet

BASE_URL = 'https://mars.tetras-lab.io'
DASHBOARD_NUM = '1'
onto_prefix="ontologyTarget"

AMR_MODEL_PATH = config['LIB']['AMR_MODEL_PATH']
AMRLD_PATH = config['LIB']['AMRLD_PATH']
owl2vowlPath = config['LIB']['owl2vowlPath']
WEBVOWL_PATH = config['LIB']['WEBVOWL_PATH']

MEDIA_PATH = "/opt/dashboards/media/"+DASHBOARD_NUM+"/"
MEDIA_URL = BASE_URL+"/dashboard/"+DASHBOARD_NUM+"/media/"


# The following is basically `import tenet`
#spec=importlib.util.spec_from_file_location("tenet",TENET_PATH+'tenet/__init__.py')
#tenet = importlib.util.module_from_spec(spec)
#spec.loader.exec_module(tenet)

In [ ]:
#stog = amrlib.load_stog_model(model_dir="/opt/dashboards/TetrasMARS/corpus/cm-tool/amrModel/model_parse_xfm_bart_large-v0_1_0")  
    


#prefixPath = uuidDirPath+"file"
#penmanPath = prefixPath+".amr.penman"
#svgPath = prefixPath+".amr.svg"
#ttlFilePath = uuidDirPath+onto_prefix+"-0/"+onto_prefix+"_factoid.ttl"


In [ ]:
def clean_sting(string):
    """ Sentence cleanup as needed """
    return re.sub("(\.)*\\n", "", string)

def string2amr(string,stog):
    stog_result = stog.parse_sents([clean_sting(string)], add_metadata=True)   
    return stog_result[0] 



def show_svg(path):
    display(SVG(filename=path))
    
def add_id_in_penman_if_needed(penmanStr,uuidStr):
    if not(penmanStr.startswith('# ::id')):
        penmanStr = '# ::id '+uuidStr+'\n'+penmanStr
    return penmanStr

def owl2vowl(ttlFilePath, webvowlFileName, webvowlFilePath, uuid='', importList=[]):
    # Run java parser
    if importList == []:
        cmd = ['java', '-jar', owl2vowlPath,
           '-file', ttlFilePath]  
    else:
        cmd = ['java', '-jar', owl2vowlPath,
           '-file', ttlFilePath,
           '-dependencies'] + importList 
    with Popen(cmd, stdout=PIPE, stderr=STDOUT) as p:
        p.wait()
        p.stdout.flush()
        if p.returncode != 0:
            print("Error in owl2vowl: \n\n"+p.stdout.read().decode())
    os.rename(webvowlFileName, webvowlFilePath)
    
def localImage2htmlImg(imgPath):
    with open(imgPath, "rb") as image_file:
        imageStr = image_file.read()
        root = ET.fromstring(imageStr)
        widthInt = int(root.attrib['width'].replace("pt",""))
        if widthInt > 1700 :
            widthStr = "100%"
        else:
            widthStr = str(widthInt)+"pt"
        img_data = base64.b64encode(imageStr)
        img_data = img_data.decode()
        img_data = "data:image/svg+xml;base64,{}".format(img_data)
        # ...
        return html.Img(id="tag_id", src=img_data, width=widthStr, height="100%", className="img_class")#, alt="my image"

In [ ]:
def processStr(input):
    # Define usefull variable and paths based on a uuid
    uuidStr = str(uuid.uuid4())
    uuidDirPath = "/opt/data/tmp/demo-tetras-mars/"+uuidStr+'/'
    os.mkdir(uuidDirPath)
    fullOntoPath = uuidDirPath+'full-ontology.ttl'
    ontoBySentencePath = uuidDirPath+'onto-by-sentence/'
    webvowlFileName = fullOntoPath.split('/')[-1].replace('ttl','json')
    webvowlFilePath = WEBVOWL_PATH+uuidStr+'_'+webvowlFileName
    uuidZipPath = MEDIA_PATH+uuidStr # without the .zip extention
    uuidZipUrl = MEDIA_URL+uuidStr+".zip"
    
    # Generate an AMR graph by sentence in a subfolder (with companion files such as images of the graphs)
    try: 
        amr_graph_list = amrbatch.parse_document_string_to_produce_amr_graph(
                         input, None, amr_model_path=AMR_MODEL_PATH, output_dirpath=uuidDirPath, 
                         amrld_serialization=True)
    except:
        errorStr = "Error generating AMR graphs. You can try a simpler input. Sorry :("
    
    # Construct ontologies from each AMR graph plus a "full" one that is the union
    try:
        factoids = tenet.create_ontology_from_amrld_dir(
                    uuidDirPath,
                    onto_prefix="http://ontologies",
                    out_file_path=fullOntoPath,
                    technical_dir_path=ontoBySentencePath)
        owl2vowl(fullOntoPath, webvowlFileName, webvowlFilePath, uuid=uuidStr)
        errorStr = ""
    except:
        errorStr = "Error generating ontology. You can still clic this link to download AMR graphs or see them below. Try a simpler input, sorry :("
    
    # Create a zip file so the user can download all generated files
    shutil.make_archive(uuidZipPath, 'zip', uuidDirPath)
    return uuidDirPath, uuidZipUrl, webvowlFilePath, errorStr

In [ ]:
##################################################################################################
# THE FOLLOWING PART IS SPECIFIC TO TÉTRAS LAB
#
# The _get_tl_config function gets configuration parameters for your
# Tétras Lab instance.
# Those parameters are passed when initialising the Dash app.
##################################################################################################
def _get_tl_config():
    import socket, errno, os
    # Find a free port
    host = "0.0.0.0"
    port = 8050
    end = 9999
    found = False
    while not found:
        with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as s:
            try:
                s.bind((host, port))
                found = True
            except socket.error as e:
                if e.errno == errno.EADDRINUSE:
                    port = port + 1
                    if (port > end):
                        raise "No available APP port"
                else:
                    raise e
    if (os.getenv("HOST", None) is not None):
        proto = os.getenv("PROTO")
        actualhost = os.getenv("JUPYTER_HOST", os.getenv("VOILA_HOST", ""))
        localport = os.getenv("PORT", 80)
        intermediatehost = os.getenv("HOST", "localhost")
        base_path = f"/{actualhost}/app_proxy/{port}/"
        proxified= f"{proto}://{intermediatehost}:{localport}{base_path}"
        localurl = f"http://{host}:{port}"
        proxy = f"{localurl}::{proxified}"
        return ((proxified, host, port, proxy, base_path))
    return ((f"http://localhost:{port}", host, port, None, "/"))

server_url, host, port, proxy, base_path = _get_tl_config()

app = Dash(
    requests_pathname_prefix=base_path,
    external_stylesheets=[dbc.themes.BOOTSTRAP]
)
##################################################################################################


##################################################################################################
# THE FOLLOWING PART IS GENERIC (JUPYTER)-DASH CODE FROM https://dash.plotly.com/basic-callbacks
#
# The _get_tl_config function gets configuration parameters for your
# Tétras Lab instance.
# Those parameters are passed when initialising the Dash app.
##################################################################################################

app.layout = html.Div([
    html.H4("Enter an english text and click on the button bellow to construct an ontology.", style={'text-align': 'center'}),
    html.Br(),
    html.P("It should take about 10 to 30 sec/sentence. You can then browse the results online or download them as a zip file.", style={'text-align': 'center'}),
    html.P("The text must be a simple succession of sentences. Fancy formating is not supported at the moment. ", style={'text-align': 'center'}),    
    html.Br(),
    html.Br(),
    html.Div(dbc.Textarea(
        id='textarea-state',
        value='The Solar System is the gravitationally bound system of the Sun. The inner system planets are terrestrial planets composed of rock and metal. The outer system planets are giant planets. The two largest planets, Jupiter and Saturn, are gas giants, being composed of hydrogen and helium.',style={'width': '100%', 'height': 130}),
        style={'width': '60%', 'height': 130, 'margin-left': 'auto', 'margin-right': 'auto'},
    ),
    html.Br(), html.Br(),
    html.Div(
        dbc.Button('Construct AMR graphs and ontology', id='textarea-state-button', n_clicks=0, outline=True, color="primary"),
        className="text-center"),
    html.Br(),
    dcc.Loading(html.Div(html.A(children="", href='', target="_blank",id="download-link"), className="text-center")),
    html.Br(),
    html.Br(),
    dcc.Loading(html.Div(id='my-output'), type='circle'),
])

@app.callback(
    #Output('textarea-state-output', 'children'),
    Output(component_id='my-output', component_property='children'),
    Output(component_id='download-link', component_property='children'),
    Output(component_id='download-link', component_property='href'),    
    Input('textarea-state-button', 'n_clicks'),
    State('textarea-state', 'value'),
    prevent_initial_call=True,
)
def update_output(n_clicks, value):
    if n_clicks > 0:
        uuidDirPath, uuidZipUrl, webvowlFilePath, errorStr = processStr(value)
        if "Error" in errorStr:
            feedbackStr = errorStr
        else:
            feedbackStr = "Download Zip File"
        #show_svg(svgPath) 
        #display(IFrame(BASE_URL+'''/webvowl/#{}">'''.format(webvowlFilePath.replace("/opt/webvowl/","").replace(".json","")),800,1200))
        return  [dbc.Row([dbc.Col(),
        dbc.Col(dbc.Accordion(  
            [dbc.AccordionItem(
                [
                    localImage2htmlImg(svgPath)
                ],
                title="AMR Graph for sentence "+re.sub(r'.document.*', '', svgPath.replace(uuidDirPath+"document-","")),
            )
             for svgPath in sorted(glob(uuidDirPath+"document-*/*.svg"))
            ]+
            [dbc.AccordionItem(
                [
                    "You can click a class to see its instances in the right panel, they are not shown in the graph.",
                    html.Br(),
                    html.A(children="Open ontology browser in separate tab.", href=BASE_URL+'''/webvowl/#{}'''.format(webvowlFilePath.replace("/opt/webvowl/","").replace(".json","")), target="_blank",id="webvowl-link"),
                    html.Br(),
                    html.Iframe(src=BASE_URL+'''/webvowl/#{}'''.format(webvowlFilePath.replace("/opt/webvowl/","").replace(".json","")),style={"height": "800px", "width": "100%"}),
                ],
                title="Browse ontology", item_id='onto'
            )
        ] , active_item='onto'), width=10), dbc.Col()
                         ]),
                 feedbackStr, uuidZipUrl
                ]

#@app.callback(
#    Output("download-zip", "data"),
#    Input("download-zip-button", "n_clicks"),
#    prevent_initial_call=True,
#)
#def func(n_clicks):
#    if n_clicks > 0:
#        return dcc.send_file(BASE_URL+'/dashboard/17/media/9f7287d0-e7b2-4328-9137-7a7c44225b68.zip')
    

    
app.run_server(mode="inline",
               #mode="external",
               host=host, port=port, proxy=proxy, height=2000)
##################################################################################################
